In [0]:
destination_path = "/dbfs/mnt/bde-assignment2/nyc_taxi_final.parquet"

nyc_taxi = spark.read.parquet(destination_path)

In [0]:
nyc_taxi.printSchema()

root
 |-- DOLocationID: long (nullable = true)
 |-- PULocationID: long (nullable = true)
 |-- VendorID: long (nullable = true)
 |-- pickup_datetime: timestamp (nullable = true)
 |-- dropoff_datetime: timestamp (nullable = true)
 |-- passenger_count: double (nullable = true)
 |-- trip_distance: double (nullable = true)
 |-- RatecodeID: double (nullable = true)
 |-- store_and_fwd_flag: string (nullable = true)
 |-- payment_type: double (nullable = true)
 |-- fare_amount: double (nullable = true)
 |-- extra: double (nullable = true)
 |-- mta_tax: double (nullable = true)
 |-- tip_amount: double (nullable = true)
 |-- tolls_amount: double (nullable = true)
 |-- improvement_surcharge: double (nullable = true)
 |-- total_amount: double (nullable = true)
 |-- congestion_surcharge: double (nullable = true)
 |-- airport_fee: double (nullable = true)
 |-- trip_distance_km: double (nullable = true)
 |-- trip_duration: double (nullable = true)
 |-- speed_kmh: double (nullable = true)
 |-- taxi_typ

In [0]:
nyc_taxi.createOrReplaceTempView("nyc_taxi_view")

In [0]:
#Divide yearly view to execute queries for a single year.

from pyspark.sql import functions as F

df_with_time = nyc_taxi.withColumn("year", F.year(F.col("pickup_datetime"))) \
                 .withColumn("month", F.month(F.col("pickup_datetime"))) \
                 .withColumn("hour", F.hour(F.col("pickup_datetime"))) \
                 .withColumn("weekday", F.date_format(F.col("pickup_datetime"), "E"))  

# Loop through each year and create a view
for year in range(2015, 2023):
    yearly_df = df_with_time.filter(F.col("year") == year)
    view_name = f"nyc_taxi_{year}_view"
    yearly_df.createOrReplaceTempView(view_name)
    print(f"View created: {view_name}")


View created: nyc_taxi_2015_view
View created: nyc_taxi_2016_view
View created: nyc_taxi_2017_view
View created: nyc_taxi_2018_view
View created: nyc_taxi_2019_view
View created: nyc_taxi_2020_view
View created: nyc_taxi_2021_view
View created: nyc_taxi_2022_view


Question 1

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2015_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2015-01 13918002 Fri 19 1.64 15.51 12.78 2015-02 13683145 Fri 19 1.63 15.69 12.92 2015-03 14705118 Sun 0 1.63 16.15 13.28 2015-04 14387195 Thu 19 1.64 16.25 13.34 2015-05 14591289 Fri 19 1.64 16.69 13.65 2015-06 13625028 Tue 19 1.64 16.59 13.58 2015-07 12789029 Wed 19 1.66 16.31 13.29 2015-08 12360445 Sat 23 1.65 16.37 13.33 2015-09 12389646 Wed 19 1.64 16.6 13.57 2015-10 13583515 Fri 19 1.63 16.68 13.68 2015-11 12502363 Sun 1 1.63 16.55 13.59 2015-12 12713292 Thu 21 1.64 16.48 13.44

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2016_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2016-01 12037880 Fri 19 1.63 15.94 13.1 2016-02 12561941 Mon 18 1.62 15.9 13.13 2016-03 13440179 Thu 19 1.62 16.23 13.36 2016-04 13125392 Sat 23 1.62 16.42 13.52 2016-05 13028346 Tue 18 1.62 16.82 13.8 2016-06 12210553 Thu 21 1.62 16.85 13.84 2016-07 11320573 Fri 18 1.63 16.67 13.65 2016-08 10896966 Wed 19 1.63 16.57 13.56 2016-09 10976422 Fri 19 1.62 17.01 14.01 2016-10 11793896 Sat 19 1.61 16.72 13.78 2016-11 10943523 Tue 19 1.61 16.66 13.75 2016-12 11350878 Fri 19 1.62 16.36 13.43

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2017_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2017-01 10498951 Tue 18 1.6 15.69 12.97 2017-02 9926967 Fri 19 1.6 15.84 13.1 2017-03 1111622 Fri 18 1.37 14.22 12.76 2017-04 10829709 Sat 19 1.59 16.53 13.66 2017-05 10861276 Wed 19 1.6 16.86 13.91 2017-06 10348168 Thu 21 1.6 16.73 13.83 2017-07 9242428 Mon 18 1.61 16.5 13.56 2017-08 9040261 Tue 18 1.61 16.54 13.59 2017-09 9558753 Fri 19 1.6 16.72 13.79 2017-10 10409567 Tue 18 1.6 16.77 13.86 2017-11 9877960 Wed 18 1.6 16.53 13.66 2017-12 10115425 Fri 19 1.61 16.36 13.43

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2018_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2018-01 9292787 Wed 18 1.6 15.75 13.03 2018-02 9013844 Fri 18 1.58 15.76 13.1 2018-03 9982224 Thu 18 1.59 16.24 13.46 2018-04 9833905 Mon 18 1.59 16.54 13.71 2018-05 9750567 Thu 19 1.59 16.92 14.02 2018-06 9192803 Fri 19 1.58 16.91 14.02 2018-07 8294162 Tue 18 1.59 16.95 14.03 2018-08 8290847 Wed 18 1.59 16.77 13.8 2018-09 8480056 Sat 18 1.58 17.09 14.14 2018-10 9288562 Tue 18 1.57 17.2 14.25 2018-11 8560523 Fri 18 1.57 17.1 14.17 2018-12 8637938 Mon 18 1.58 16.96 13.86

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2019_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2019-01 8120841 Thu 18 1.57 16.27 13.36 2019-02 7443920 Fri 18 1.57 19.13 15.73 2019-03 8269729 Fri 18 1.57 19.58 16.11 2019-04 7821425 Tue 18 1.57 19.73 16.06 2019-05 7908173 Thu 18 1.57 19.91 16.31 2019-06 7246538 Sat 17 1.56 20.03 16.47 2019-07 6556984 Tue 18 1.58 19.82 16.17 2019-08 6301972 Thu 18 1.57 19.98 16.26 2019-09 6782590 Thu 19 1.56 20.1 16.49 2019-10 7446104 Wed 18 1.55 20.07 16.45 2019-11 7065637 Fri 18 1.54 19.74 16.23 2019-12 7093605 Tue 18 1.55 19.98 16.3

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2020_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2020-01 6626745 Thu 18 1.53 19.17 15.71 2020-02 6486123 Fri 18 1.51 19.16 15.85 2020-03 3122173 Mon 18 1.49 18.73 15.7 2020-04 257641 Wed 15 1.31 17.93 14.59 2020-05 382865 Fri 16 1.32 21.29 14.94 2020-06 577935 Tue 12 1.37 22.6 15.78 2020-07 823716 Thu 14 1.39 22.58 15.48 2020-08 1032563 Mon 14 1.42 22.34 15.45 2020-09 1367842 Wed 15 1.44 18.97 15.06 2020-10 1705767 Thu 15 1.45 19.3 15.49 2020-11 1536905 Mon 15 1.44 18.94 15.08 2020-12 1485722 Tue 14 1.45 19.08 15.17

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2021_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2021-01 1388274 Fri 15 1.44 19.33 15.43 2021-02 1378572 Wed 14 1.43 19.2 15.4 2021-03 1935287 Wed 17 1.43 19.51 15.66 2021-04 2175705 Fri 14 1.43 20.3 16.5 2021-05 2506068 Sat 14 1.45 20.55 16.67 2021-06 2825584 Wed 18 1.46 20.89 16.99 2021-07 2807043 Thu 18 1.48 21.4 17.25 2021-08 2774457 Tue 18 1.47 21.59 17.45 2021-09 2941530 Wed 18 1.45 22.0 17.95 2021-10 3462228 Fri 18 1.44 21.43 17.66 2021-11 3474935 Tue 18 1.44 21.78 17.94 2021-12 3207541 Wed 18 1.45 21.95 17.96

In [0]:
%sql

SELECT 
    CONCAT(year, '-', LPAD(month, 2, '0')) AS year_month,
    SUM(trips_count) AS total_trips,
    MAX(CASE WHEN weekday_rank = 1 THEN weekday ELSE NULL END) AS most_trips_day,  
    MAX(CASE WHEN hour_rank = 1 THEN hour ELSE NULL END) AS most_trips_hour,
    ROUND(AVG(avg_passengers), 2) AS avg_passengers,  
    ROUND(AVG(avg_amount_per_trip), 2) AS avg_amount_per_trip,  
    ROUND(AVG(avg_amount_per_passenger), 2) AS avg_amount_per_passenger  
FROM (
    SELECT
        year, 
        month,
        weekday,
        hour,
        COUNT(*) AS trips_count,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(weekday) DESC) AS weekday_rank,
        RANK() OVER (PARTITION BY month ORDER BY COUNT(hour) DESC) AS hour_rank,
        AVG(passenger_count) AS avg_passengers,
        AVG(total_amount) AS avg_amount_per_trip,
        AVG(total_amount / passenger_count) AS avg_amount_per_passenger
    FROM nyc_taxi_2022_view
    GROUP BY year, month, weekday, hour
) trips_agg
GROUP BY year, month;


year_month total_trips most_trips_day most_trips_hour avg_passengers avg_amount_per_trip avg_amount_per_passenger 2022-01 2444914 Mon 15 1.41 20.15 17.2 2022-02 2955493 Fri 18 1.4 20.39 17.39 2022-03 3591421 Thu 18 1.41 21.65 18.38 2022-04 3562328 Fri 18 1.42 22.32 18.73 2022-05 3543372 Tue 18 1.41 22.97 19.27 2022-06 3500300 Thu 18 1.42 23.08 19.28 2022-07 3123896 Fri 18 1.44 22.42 18.64 2022-08 3101017 Tue 18 1.43 22.52 18.78 2022-09 3132017 Fri 18 1.4 23.34 19.67 2022-10 3603146 Mon 18 1.39 23.08 19.51 2022-11 3182674 Tue 18 1.4 22.91 19.28 2022-12 3328376 Thu 18 1.42 25.66 21.21

In [0]:
yellow_taxi = nyc_taxi.filter(F.col("taxi_type") == "yellow")
yellow_taxi.createOrReplaceTempView("yellow_taxi_view")

green_taxi = nyc_taxi.filter(F.col("taxi_type") == "green")
green_taxi.createOrReplaceTempView("green_taxi_view")

Question 2

In [0]:
%sql

SELECT 
    ROUND(AVG(trip_duration), 2) AS avg_trip_duration,
    ROUND(PERCENTILE(trip_duration, 0.5), 2) AS median_trip_duration,
    ROUND(MIN(trip_duration),2) AS min_trip_duration,
    ROUND(MAX(trip_duration),2) AS max_trip_duration,
    ROUND(AVG(trip_distance_km), 2) AS avg_trip_distance_km,
    ROUND(PERCENTILE(trip_distance_km, 0.5), 2) AS median_trip_distance_km,
    ROUND(MIN(trip_distance_km),2) AS min_trip_distance_km,
    ROUND(MAX(trip_distance_km),2) AS max_trip_distance_km,
    ROUND(AVG(trip_distance_km), 2) AS avg_trip_distance_km,
    ROUND(PERCENTILE(trip_distance_km, 0.5), 2) AS median_trip_distance_km,
    ROUND(MIN(trip_distance_km),2) AS min_trip_distance_km,
    ROUND(MAX(trip_distance_km),2) AS max_trip_distance_km,
    ROUND(AVG(speed_kmh), 2) AS avg_speed_kmh,
    ROUND(PERCENTILE(speed_kmh, 0.5), 2) AS median_speed_kmh,
    ROUND(MIN(speed_kmh),2) AS min_speed_kmh,
    ROUND(MAX(speed_kmh),2) AS max_speed_kmh

FROM yellow_taxi_view

avg_trip_duration median_trip_duration min_trip_duration max_trip_duration avg_trip_distance_km median_trip_distance_km min_trip_distance_km max_trip_distance_km avg_trip_distance_km median_trip_distance_km min_trip_distance_km max_trip_distance_km avg_speed_kmh median_speed_kmh min_speed_kmh max_speed_kmh 14.55 11.4 1.0 120.0 4.93 2.75 0.51 79.98 4.93 2.75 0.51 79.98 18.83 16.53 0.27 199.99

In [0]:
%sql

SELECT 
    ROUND(AVG(trip_duration), 2) AS avg_trip_duration,
    ROUND(PERCENTILE(trip_duration, 0.5), 2) AS median_trip_duration,
    ROUND(MIN(trip_duration),2) AS min_trip_duration,
    ROUND(MAX(trip_duration),2) AS max_trip_duration,
    ROUND(AVG(trip_distance_km), 2) AS avg_trip_distance_km,
    ROUND(PERCENTILE(trip_distance_km, 0.5), 2) AS median_trip_distance_km,
    ROUND(MIN(trip_distance_km),2) AS min_trip_distance_km,
    ROUND(MAX(trip_distance_km),2) AS max_trip_distance_km,
    ROUND(AVG(trip_distance_km), 2) AS avg_trip_distance_km,
    ROUND(PERCENTILE(trip_distance_km, 0.5), 2) AS median_trip_distance_km,
    ROUND(MIN(trip_distance_km),2) AS min_trip_distance_km,
    ROUND(MAX(trip_distance_km),2) AS max_trip_distance_km,
    ROUND(AVG(speed_kmh), 2) AS avg_speed_kmh,
    ROUND(PERCENTILE(speed_kmh, 0.5), 2) AS median_speed_kmh,
    ROUND(MIN(speed_kmh),2) AS min_speed_kmh,
    ROUND(MAX(speed_kmh),2) AS max_speed_kmh

FROM green_taxi_view

avg_trip_duration median_trip_duration min_trip_duration max_trip_duration avg_trip_distance_km median_trip_distance_km min_trip_distance_km max_trip_distance_km avg_trip_distance_km median_trip_distance_km min_trip_distance_km max_trip_distance_km avg_speed_kmh median_speed_kmh min_speed_kmh max_speed_kmh 14.06 10.82 1.0 120.0 4.96 3.17 0.51 99.96 4.96 3.17 0.51 99.96 20.36 18.42 0.26 199.96

Question 3

In [0]:
%sql

SELECT
    pickup_borough,
    dropoff_borough,
    month,
    day_of_week,
    hour,   
    SUM(trips_count) AS total_trips, 
    ROUND(AVG(trip_distance_km),2) AS avg_distance_km,  -- Average distance in km
    ROUND(AVG(avg_amount), 2) AS avg_amount_per_trip,  -- Average amount paid per trip
    ROUND(SUM(amount_paid),2) AS total_amount_paid  -- Total amount paid
FROM (
    SELECT 
        pickup_borough,
        dropoff_borough,
        MONTH(pickup_datetime) AS month,
        DAYOFWEEK(pickup_datetime) AS day_of_week,
        HOUR(pickup_datetime) AS hour,
        COUNT(*) AS trips_count,
        AVG(trip_distance_km) AS trip_distance_km,
        AVG(total_amount) AS avg_amount,
        SUM(total_amount) AS amount_paid
    FROM yellow_taxi_view
    GROUP BY pickup_borough, dropoff_borough, MONTH(pickup_datetime), DAYOFWEEK(pickup_datetime), HOUR(pickup_datetime)
) AS aggregated_data
GROUP BY pickup_borough, dropoff_borough, month, day_of_week, hour
ORDER BY pickup_borough, dropoff_borough, month, day_of_week, hour

pickup_borough dropoff_borough month day_of_week hour total_trips avg_distance_km avg_amount_per_trip total_amount_paid Bronx Bronx 1 1 0 269 4.19 12.58 3385.26 Bronx Bronx 1 1 1 303 4.97 13.79 4178.34 Bronx Bronx 1 1 2 277 4.38 12.67 3509.83 Bronx Bronx 1 1 3 283 4.75 13.07 3699.61 Bronx Bronx 1 1 4 319 4.6 13.2 4209.55 Bronx Bronx 1 1 5 223 4.75 13.39 2986.97 Bronx Bronx 1 1 6 161 4.86 13.81 2223.67 Bronx Bronx 1 1 7 186 5.22 15.75 2929.43 Bronx Bronx 1 1 8 331 5.01 16.52 5468.77 Bronx Bronx 1 1 9 428 5.3 17.28 7395.33 Bronx Bronx 1 1 10 379 5.37 17.66 6694.36 Bronx Bronx 1 1 11 290 4.47 15.19 4406.12 Bronx Bronx 1 1 12 248 4.37 16.41 4069.02 Bronx Bronx 1 1 13 240 5.81 19.04 4568.97 Bronx Bronx 1 1 14 255 5.71 19.14 4880.93 Bronx Bronx 1 1 15 220 5.71 18.05 3971.89 Bronx Bronx 1 1 16 151 5.47 17.41 2628.61 Bronx Bronx 1 1 17 202 4.53 15.48 3127.11 Bronx Bronx 1 1 18 174 5.41 17.51 3047.23 Bronx Bronx 1 1 19 156 5.11 17.21 2684.35 Bronx Bronx 1 1 20 165 5.16 16.6 2739.76 Bronx Bronx 1 1 21 127 5.6 16.3 2070.47 Bronx Bronx 1 1 22 140 5.01 14.86 2080.07 Bronx Bronx 1 1 23 147 4.72 14.97 2200.46 Bronx Bronx 1 2 0 174 4.35 12.2 2123.57 Bronx Bronx 1 2 1 159 4.32 12.78 2032.12 Bronx Bronx 1 2 2 144 4.16 12.4 1786.04 Bronx Bronx 1 2 3 109 4.48 13.59 1481.18 Bronx Bronx 1 2 4 136 4.7 14.68 1996.57 Bronx Bronx 1 2 5 156 5.51 16.69 2603.87 Bronx Bronx 1 2 6 154 5.59 16.51 2542.67 Bronx Bronx 1 2 7 291 4.69 15.95 4642.32 Bronx Bronx 1 2 8 382 4.95 17.79 6796.3 Bronx Bronx 1 2 9 335 5.48 19.96 6685.73 Bronx Bronx 1 2 10 293 6.15 21.44 6281.05 Bronx Bronx 1 2 11 264 5.2 18.19 4802.87 Bronx Bronx 1 2 12 265 5.85 19.78 5241.15 Bronx Bronx 1 2 13 304 5.03 18.96 5764.81 Bronx Bronx 1 2 14 278 5.72 21.88 6082.45 Bronx Bronx 1 2 15 264 5.64 20.71 5466.3 Bronx Bronx 1 2 16 262 5.43 19.42 5088.53 Bronx Bronx 1 2 17 263 4.87 17.82 4685.77 Bronx Bronx 1 2 18 200 4.65 18.32 3663.11 Bronx Bronx 1 2 19 138 5.09 17.03 2350.8 Bronx Bronx 1 2 20 143 5.39 16.77 2397.76 Bronx Bronx 1 2 21 131 4.88 16.34 2140.37 Bronx Bronx 1 2 22 119 5.7 16.08 1914.01 Bronx Bronx 1 2 23 141 5.48 15.06 2123.64 Bronx Bronx 1 3 0 150 5.3 15.09 2263.81 Bronx Bronx 1 3 1 121 5.18 15.1 1826.68 Bronx Bronx 1 3 2 109 4.67 13.59 1481.48 Bronx Bronx 1 3 3 98 5.59 14.85 1455.03 Bronx Bronx 1 3 4 101 4.61 14.62 1476.2 Bronx Bronx 1 3 5 127 5.77 19.34 2456.78 Bronx Bronx 1 3 6 180 5.05 16.72 3009.42 Bronx Bronx 1 3 7 372 4.96 17.12 6368.37 Bronx Bronx 1 3 8 427 4.7 17.27 7373.35 Bronx Bronx 1 3 9 375 5.18 17.81 6680.57 Bronx Bronx 1 3 10 321 5.47 18.87 6056.08 Bronx Bronx 1 3 11 296 5.35 19.68 5825.52 Bronx Bronx 1 3 12 323 5.29 19.08 6164.18 Bronx Bronx 1 3 13 304 5.6 19.69 5986.28 Bronx Bronx 1 3 14 265 5.68 20.04 5311.34 Bronx Bronx 1 3 15 316 5.49 18.97 5995.45 Bronx Bronx 1 3 16 249 4.99 18.98 4725.56 Bronx Bronx 1 3 17 262 4.9 18.29 4792.8 Bronx Bronx 1 3 18 205 5.02 17.63 3613.28 Bronx Bronx 1 3 19 163 6.51 19.95 3252.08 Bronx Bronx 1 3 20 127 5.42 17.53 2226.19 Bronx Bronx 1 3 21 138 5.47 16.38 2260.1 Bronx Bronx 1 3 22 141 5.97 16.65 2346.99 Bronx Bronx 1 3 23 166 5.66 15.97 2650.93 Bronx Bronx 1 4 0 141 4.42 13.26 1870.08 Bronx Bronx 1 4 1 118 5.09 14.7 1734.31 Bronx Bronx 1 4 2 107 4.57 14.6 1562.15 Bronx Bronx 1 4 3 79 4.98 14.81 1170.31 Bronx Bronx 1 4 4 89 4.88 16.42 1461.4 Bronx Bronx 1 4 5 130 5.53 18.51 2406.25 Bronx Bronx 1 4 6 150 5.83 17.6 2639.69 Bronx Bronx 1 4 7 308 5.21 17.01 5240.34 Bronx Bronx 1 4 8 415 5.54 18.84 7817.24 Bronx Bronx 1 4 9 334 5.38 18.93 6322.64 Bronx Bronx 1 4 10 339 5.64 19.38 6571.13 Bronx Bronx 1 4 11 326 5.62 18.99 6192.16 Bronx Bronx 1 4 12 310 5.76 20.02 6205.06 Bronx Bronx 1 4 13 340 5.6 19.46 6617.97 Bronx Bronx 1 4 14 323 5.93 20.57 6642.98 Bronx Bronx 1 4 15 286 5.62 19.23 5500.01 Bronx Bronx 1 4 16 228 4.97 18.88 4303.98 Bronx Bronx 1 4 17 242 5.35 19.13 4628.53 Bronx Bronx 1 4 18 227 5.41 19.13 4341.45 Bronx Bronx 1 4 19 176 5.36 18.29 3218.64 Bronx Bronx 1 4 20 123 5.39 16.73 2057.73 Bronx Bronx 1 4 21 152 6.57 20.21 3071.18 Br

In [0]:
%sql

SELECT
    pickup_borough,
    dropoff_borough,
    month,
    day_of_week,
    hour,   
    SUM(trips_count) AS total_trips, 
    ROUND(AVG(trip_distance_km),2) AS avg_distance_km,  -- Average distance in km
    ROUND(AVG(avg_amount), 2) AS avg_amount_per_trip,  -- Average amount paid per trip
    ROUND(SUM(amount_paid),2) AS total_amount_paid  -- Total amount paid
FROM (
    SELECT 
        pickup_borough,
        dropoff_borough,
        MONTH(pickup_datetime) AS month,
        DAYOFWEEK(pickup_datetime) AS day_of_week,
        HOUR(pickup_datetime) AS hour,
        COUNT(*) AS trips_count,
        AVG(trip_distance_km) AS trip_distance_km,
        AVG(total_amount) AS avg_amount,
        SUM(total_amount) AS amount_paid
    FROM green_taxi_view
    GROUP BY pickup_borough, dropoff_borough, MONTH(pickup_datetime), DAYOFWEEK(pickup_datetime), HOUR(pickup_datetime)
) AS aggregated_data
GROUP BY pickup_borough, dropoff_borough, month, day_of_week, hour
ORDER BY pickup_borough, dropoff_borough, month, day_of_week, hour

pickup_borough dropoff_borough month day_of_week hour total_trips avg_distance_km avg_amount_per_trip total_amount_paid Bronx Bronx 1 1 0 1172 3.88 11.28 13216.42 Bronx Bronx 1 1 1 1033 4.09 11.89 12278.94 Bronx Bronx 1 1 2 797 4.09 11.77 9379.03 Bronx Bronx 1 1 3 641 4.08 11.77 7547.4 Bronx Bronx 1 1 4 585 4.5 12.39 7250.61 Bronx Bronx 1 1 5 334 3.9 11.65 3889.95 Bronx Bronx 1 1 6 277 4.4 12.46 3452.43 Bronx Bronx 1 1 7 465 4.78 13.92 6470.97 Bronx Bronx 1 1 8 755 4.96 14.87 11224.04 Bronx Bronx 1 1 9 1124 4.95 14.47 16261.17 Bronx Bronx 1 1 10 1238 4.94 14.33 17736.1 Bronx Bronx 1 1 11 1132 4.48 13.36 15128.54 Bronx Bronx 1 1 12 1204 4.59 13.88 16716.18 Bronx Bronx 1 1 13 1262 5.04 14.74 18598.31 Bronx Bronx 1 1 14 1286 4.85 14.42 18539.99 Bronx Bronx 1 1 15 1328 4.63 13.61 18075.57 Bronx Bronx 1 1 16 1164 4.67 13.2 15366.83 Bronx Bronx 1 1 17 1292 4.42 12.98 16771.05 Bronx Bronx 1 1 18 1155 4.46 12.96 14965.62 Bronx Bronx 1 1 19 1088 4.41 12.6 13705.69 Bronx Bronx 1 1 20 965 4.19 12.85 12403.07 Bronx Bronx 1 1 21 880 4.2 12.42 10931.51 Bronx Bronx 1 1 22 769 4.0 11.67 8974.55 Bronx Bronx 1 1 23 713 3.85 11.36 8102.32 Bronx Bronx 1 2 0 501 3.61 10.99 5504.93 Bronx Bronx 1 2 1 394 3.85 11.35 4472.15 Bronx Bronx 1 2 2 215 4.27 12.24 2630.96 Bronx Bronx 1 2 3 175 4.0 11.82 2067.75 Bronx Bronx 1 2 4 228 4.54 14.58 3323.62 Bronx Bronx 1 2 5 287 5.48 17.12 4912.98 Bronx Bronx 1 2 6 503 5.12 15.27 7682.84 Bronx Bronx 1 2 7 1582 4.54 14.33 22664.46 Bronx Bronx 1 2 8 2393 4.32 13.91 33295.33 Bronx Bronx 1 2 9 2157 4.51 14.49 31256.47 Bronx Bronx 1 2 10 1773 4.83 14.74 26137.56 Bronx Bronx 1 2 11 1717 4.92 15.1 25918.34 Bronx Bronx 1 2 12 1682 4.87 14.59 24533.99 Bronx Bronx 1 2 13 1724 4.65 14.44 24892.3 Bronx Bronx 1 2 14 1850 4.67 14.66 27118.8 Bronx Bronx 1 2 15 1890 4.64 14.58 27550.59 Bronx Bronx 1 2 16 1839 4.34 14.4 26485.48 Bronx Bronx 1 2 17 1770 4.25 14.0 24775.28 Bronx Bronx 1 2 18 1500 3.96 13.01 19508.59 Bronx Bronx 1 2 19 1193 3.85 12.38 14763.64 Bronx Bronx 1 2 20 928 4.22 12.51 11607.27 Bronx Bronx 1 2 21 802 4.0 12.18 9768.79 Bronx Bronx 1 2 22 662 3.95 11.88 7865.13 Bronx Bronx 1 2 23 651 4.3 12.49 8129.1 Bronx Bronx 1 3 0 518 3.87 11.53 5973.36 Bronx Bronx 1 3 1 318 3.91 11.56 3676.12 Bronx Bronx 1 3 2 195 3.77 11.53 2248.83 Bronx Bronx 1 3 3 128 3.97 11.64 1490.27 Bronx Bronx 1 3 4 131 5.39 15.38 2014.17 Bronx Bronx 1 3 5 244 6.13 17.93 4375.98 Bronx Bronx 1 3 6 597 5.64 16.91 10094.77 Bronx Bronx 1 3 7 1690 4.61 14.84 25081.72 Bronx Bronx 1 3 8 2595 4.17 13.88 36017.75 Bronx Bronx 1 3 9 2337 4.65 14.57 34056.71 Bronx Bronx 1 3 10 2003 4.88 14.81 29654.94 Bronx Bronx 1 3 11 1964 5.11 15.51 30451.95 Bronx Bronx 1 3 12 2011 5.05 15.52 31210.17 Bronx Bronx 1 3 13 1887 4.96 15.05 28405.33 Bronx Bronx 1 3 14 1980 4.72 14.93 29566.85 Bronx Bronx 1 3 15 2109 4.84 15.04 31716.55 Bronx Bronx 1 3 16 2012 4.55 15.3 30788.43 Bronx Bronx 1 3 17 1974 4.55 15.12 29841.91 Bronx Bronx 1 3 18 1677 4.04 13.49 22615.5 Bronx Bronx 1 3 19 1368 4.21 13.3 18200.02 Bronx Bronx 1 3 20 1075 4.22 12.85 13810.26 Bronx Bronx 1 3 21 944 3.89 11.96 11290.37 Bronx Bronx 1 3 22 708 4.28 12.64 8951.81 Bronx Bronx 1 3 23 661 4.52 12.82 8476.24 Bronx Bronx 1 4 0 522 4.03 12.08 6305.16 Bronx Bronx 1 4 1 322 3.65 11.37 3661.46 Bronx Bronx 1 4 2 189 4.58 13.34 2520.41 Bronx Bronx 1 4 3 105 4.15 11.57 1214.86 Bronx Bronx 1 4 4 154 4.94 15.45 2378.76 Bronx Bronx 1 4 5 240 6.35 18.21 4369.49 Bronx Bronx 1 4 6 645 5.62 16.23 10470.49 Bronx Bronx 1 4 7 1885 4.71 14.94 28159.26 Bronx Bronx 1 4 8 2879 4.38 13.92 40087.99 Bronx Bronx 1 4 9 2528 4.64 14.66 37066.42 Bronx Bronx 1 4 10 2178 4.85 15.01 32689.85 Bronx Bronx 1 4 11 2124 4.98 15.07 32001.97 Bronx Bronx 1 4 12 2029 4.97 14.95 30339.66 Bronx Bronx 1 4 13 2077 5.0 15.04 31228.4 Bronx Bronx 1 4 14 2240 4.86 15.01 33630.04 Bronx Bronx 1 4 15 2257 4.75 15.02 33909.47 Bronx Bronx 1 4 16 2096 4.55 15.06 31574.56 Bronx Bronx 1 4 17 2095 4.35 14.61 30617.84 Bronx Bronx 1 4 18 1976 4.15 13.52 26719.98 Bronx Bron

Question 4

In [0]:
%sql

SELECT 
    ROUND((SUM(CASE WHEN tip_amount > 0 THEN 1 ELSE 0 END) / COUNT(*)) * 100, 2) AS tip_percentage 
FROM nyc_taxi_view


tip_percentage 63.87

Question 5

In [0]:
%sql

SELECT 
    ROUND((SUM(CASE WHEN tip_amount >= 5 THEN 1 ELSE 0 END) / COUNT(*)) * 100, 2) AS tip_percentage 
FROM nyc_taxi_view
WHERE tip_amount > 0


tip_percentage 12.31

Question 6

In [0]:
%sql

SELECT 
    CASE 
        WHEN trip_duration < 5 THEN 'Under 5 Mins'
        WHEN trip_duration >= 5 AND trip_duration < 10 THEN '5-10 Mins'
        WHEN trip_duration >= 10 AND trip_duration < 20 THEN '10-20 Mins'
        WHEN trip_duration >= 20 AND trip_duration < 30 THEN '20-30 Mins'
        WHEN trip_duration >= 30 AND trip_duration < 60 THEN '30-60 Mins'
        ELSE '60+ Mins'
    END AS duration_bin,
    
    ROUND(AVG(speed_kmh), 2) AS avg_speed_kmh,
    ROUND(AVG(trip_distance_km / total_amount), 2) AS avg_distance_per_dollar

FROM nyc_taxi_view
WHERE trip_duration IS NOT NULL AND total_amount > 0
GROUP BY duration_bin
ORDER BY 
    CASE 
        WHEN duration_bin = 'Under 5 Mins' THEN 1
        WHEN duration_bin = '5-10 Mins' THEN 2
        WHEN duration_bin = '10-20 Mins' THEN 3
        WHEN duration_bin = '20-30 Mins' THEN 4
        WHEN duration_bin = '30-60 Mins' THEN 5
        ELSE 6
    END;

duration_bin avg_speed_kmh avg_distance_per_dollar Under 5 Mins 20.22 0.17 5-10 Mins 17.07 0.21 10-20 Mins 17.72 0.26 20-30 Mins 21.24 0.31 30-60 Mins 25.68 0.36 60+ Mins 22.67 0.46

The queries below are supporting information for the question 7

In [0]:
%sql

WITH aggregated_data AS (
    SELECT 
        taxi_type,
        pickup_borough,
        dropoff_borough,
        COUNT(*) AS trips_count
    FROM nyc_taxi_view
    WHERE trip_duration < 5
    GROUP BY taxi_type, pickup_borough, dropoff_borough
),
ranked_data AS (
    SELECT
        taxi_type,
        pickup_borough,
        dropoff_borough,
        RANK() OVER (PARTITION BY taxi_type ORDER BY trips_count DESC) AS rank_borough
    FROM aggregated_data
)

SELECT
    rd.taxi_type,
    rd.pickup_borough,
    rd.dropoff_borough,
    rd.rank_borough
FROM ranked_data rd
WHERE rd.rank_borough < 5
GROUP BY rd.taxi_type, rd.pickup_borough, rd.dropoff_borough, rd.rank_borough
ORDER BY rd.taxi_type, rd.rank_borough;


taxi_type pickup_borough dropoff_borough rank_borough green Manhattan Manhattan 1 green Queens Queens 2 green Brooklyn Brooklyn 3 green Bronx Bronx 4 yellow Manhattan Manhattan 1 yellow Queens Queens 2 yellow Brooklyn Brooklyn 3 yellow Unknown Unknown 4

In [0]:
%sql

SELECT
    HOUR(pickup_datetime) AS hour,
    taxi_type,
    pickup_borough,
    COUNT(*) AS trip_count
FROM green_taxi_view
WHERE trip_duration < 5
GROUP BY hour, taxi_type, pickup_borough
ORDER BY trip_count DESC
LIMIT 10;


hour taxi_type pickup_borough trip_count 19 green Manhattan 241848 18 green Manhattan 237806 9 green Manhattan 217477 20 green Manhattan 208710 19 green Brooklyn 206661 17 green Manhattan 206265 10 green Manhattan 200273 8 green Manhattan 199313 20 green Brooklyn 198026 21 green Brooklyn 194254

In [0]:
%sql

SELECT
    HOUR(pickup_datetime) AS hour,
    taxi_type,
    pickup_borough,
    COUNT(*) AS trip_count
FROM yellow_taxi_view
WHERE trip_duration < 5
GROUP BY hour, taxi_type, pickup_borough
ORDER BY trip_count DESC
LIMIT 10;


hour taxi_type pickup_borough trip_count 19 yellow Manhattan 5019567 18 yellow Manhattan 4775603 20 yellow Manhattan 4753788 21 yellow Manhattan 4506270 17 yellow Manhattan 4159829 22 yellow Manhattan 4122107 7 yellow Manhattan 3845725 8 yellow Manhattan 3737656 12 yellow Manhattan 3724502 16 yellow Manhattan 3713856